### Packages

In [7]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import random
import re
import warnings
import datetime
#from pandas_profiling import ProfileReport
from datetime import datetime
from sklearn.metrics import classification_report,confusion_matrix

warnings.filterwarnings("ignore")
pd.set_option('display.max_columns', None)
%matplotlib inline
sns.set(style='darkgrid')
params = {'font.family': 'Times New Roman', 'axes.labelsize': 14, 'xtick.labelsize': 14, 
          'ytick.labelsize': 14, 'axes.labelweight': 'bold'}
plt.rcParams.update(params)


### Importing Data

In [8]:
df=pd.read_excel('cctx_train.xlsx')
dtest=pd.read_excel('cctx_test.xlsx')
df=df.dropna()

In [9]:
df

Transaction_ID  Transaction_Flag        Transaction_Date  \
0            TX00002             False 2018-01-01 01:48:50.951   
1            TX00004             False 2018-01-01 09:08:52.666   
2            TX00005             False 2018-01-01 09:08:52.666   
3            TX00006             False 2018-01-01 09:45:55.969   
4            TX00007             False 2018-01-01 23:41:59.228   
...              ...               ...                     ...   
10495        TX13121             False 2018-12-31 15:47:34.782   
10496        TX13122             False 2018-12-31 15:47:34.782   
10497        TX13123             False 2018-12-31 15:47:34.782   
10498        TX13124             False 2018-12-31 15:47:34.782   
10499        TX13125             False 2018-12-31 22:11:05.961   

      Transaction_Type  Transaction_Amount  Bank_ID     CC_ID Card_Type  \
0                  T08             50000.0        1  CCID5563      CC11   
1                  T01           1000000.0        1  CCID4598      CC08   
2                  T15           1000000.0        1  CCID2839      CC08   
3                  T15           1000000.0        1  CCID2968      CC08   
4                  T10           2500000.0        1  CCID0176      CC12   
...                ...                 ...      ...       ...       ...   
10495              T13           5000000.0        1  CCID4018      CC08   
10496              T13           4800000.0        1  CCID7476      CC11   
10497              T13           2500000.0        1  CCID7625      CC00   
10498              T13           1100000.0        1  CCID6508      CC11   
10499              T02            102500.0        1  CCID5211      CC11   

       Card_Holder  Channel_ID Merchant_ID Country_ID    City_ID EDC_Type  \
0                2           1       M0001      CTY06  CTY06-133  EDC0885   
1                2           1       M0001      CTY06  CTY06-129  EDC0565   
2                2           1       M0001      CTY06  CTY06-073  EDC4639   
3                2           1       M0001      CTY06  CTY06-129  EDC3918   
4                2           1       M0001      CTY06  CTY06-133  EDC2863   
...            ...         ...         ...        ...        ...      ...   
10495            2           1       M0001      CTY06  CTY06-023  EDC0741   
10496            2           1       M0001      CTY06  CTY06-181  EDC0797   
10497            2           1       M0001      CTY06  CTY06-023  EDC0587   
10498            2           1       M0001      CTY06  CTY06-186  EDC0626   
10499            2           2       M0597      CTY06  CTY06-171  EDC4477   

      EDC_Location EDC_Owner  Average_Transaction_Amount  \
0         LEDC3703  OEDC0377                   661855.03   
1         LEDC3205  OEDC0377                  2171907.10   
2         LEDC3081  OEDC0377                  1714437.98   
3         LEDC1993  OEDC0377                 10163708.23   
4         LEDC2062  OEDC0377                   690066.65   
...            ...       ...                         ...   
10495     LEDC3813  OEDC0377                  1667486.67   
10496     LEDC3826  OEDC0377                  2530285.33   
10497     LEDC3795  OEDC0377                  1225000.00   
10498     LEDC3811  OEDC0377                   820036.79   
10499     LEDC4583  OEDC0633                   571282.15   

       Maximum_Transaction_Amount  Minimum_Transaction_Amount  \
0                      11000000.0                     24212.0   
1                      28555000.0                    100000.0   
2                       8500000.0                        50.0   
3                     100000000.0                     63000.0   
4                       3523000.0                     26500.0   
...                           ...                         ...   
10495                  20000000.0                     50000.0   
10496                   5000000.0                   1000000.0   
10497                  10000000.0                    100000.0   
10498           

### Dropping Unused Columns

In [10]:
df=df.drop(['Transaction_Flag','Bank_ID'],axis=1)

### Useful Functions

In [11]:
def timer(start_time, header='\nProgram Schedule'):
    end_time = pd.to_datetime('now', utc=True) + pd.Timedelta('07:00:00')
    print('\n\033[1m' + header + ':\033[0m')
    print(start_time.strftime('Start   : %Y-%m-%d %I:%M:%S %p'))
    print(end_time.strftime('Finish  : %Y-%m-%d %I:%M:%S %p'))
    run_time = str(end_time - start_time)
    idx1 = run_time.find(' ', 3) + 1
    idx2 = run_time.find('.')
    print('Runtime :', run_time[idx1 : idx2], '\n')
    
def category_counts(df, col, header=None, decimal=1, asc=False, top=10, style=True):
    header = col if header is None else header
    table = df[col].value_counts().rename_axis(header).reset_index(name='Count')
    table['Percentage'] = table['Count'] / table['Count'].sum(axis=0)
    
    if asc:
        table.sort_values(by=header, inplace=True)
        table.reset_index(drop=True, inplace=True)
        
    table['Cumulative'] = table['Percentage'].cumsum()
    table.index += 1
    
    table = table.head(top)
    
    if style:
        pct = '{:.' + str(decimal) + '%}'
        table = table.style.format({'Count': '{:,}', 'Percentage': pct, 'Cumulative': pct})
        
    return table

def memory_usage(df, unit='MB'):
    size = df.memory_usage(index=True, deep=True).sum()
    
    if unit == 'GB':
        print('Memory usage:', f'{size / 2**30:,.2f}', unit)
    elif unit == 'MB':
        print('Memory usage:', f'{size / 2**20:,.2f}', unit)
    else:
        print('Memory usage:', f'{size / 2**10:,.2f}', 'kB')

from scipy.stats import chi2_contingency

def target_pivot(df, var, target, count, percent=True, ncat=10, alpha=0.05, style=True):
    n = len(df[var].unique())
    
    if n <= ncat:
        pvt = pd.pivot_table(df, values=count, index=var, columns=target, aggfunc='count')
        pval = chi2_contingency(pvt)[1]
        
        print('P-value:', f'{pval:.2%}')
        
        if pval <= alpha:
            print('\033[1mConclusion:\033[0m There is a statistically significant association between\033[1m', var, 
                  '\033[0mand\033[1m', target, '\033[0m\n')
            
            print('The differences between the observed counts and the expected counts:')
            display((pvt - chi2_contingency(pvt)[3]).round(1))
            
        else:
            print('\033[1mConclusion:\033[0m There is NOT enough evidence to conclude that\033[1m', var, 
                  '\033[0mand\033[1m', target, '\033[0mare associated\n')
        
        if percent:
            cols = pvt.columns
            total = pvt.sum(1)

            for col in cols:
                pvt[col] = pvt[col] / total
                
                if col in [1, True, 'Y', 'Yes', 'YES']:
                    pos = col
                
            pvt.sort_values(by=pos, ascending=False, inplace=True) 
            
        if style:
            fmt = '{:,.2%}' if percent else '{:,}'
            pvt = pvt.style.format(fmt)
            
        print('Pivot table between variable\033[1m', var, '\033[0mand\033[1m', target, '\033[0m(in percent):')
            
        display(pvt)
    
    else:
        print('Pivot table for a high cardinality variable will not be shown.', 
              'Variable\033[1m', var, '\033[0mhas', f'{n:,}', 'unique values.')

import matplotlib

#matplotlib.use('TkAgg')

from phik import phik_from_array
from phik import outlier_significance_from_array

        
def category_boxplot(data, variable, category, threshold=0.8, plotsize=(15,7), colors=['green', 'red'], limits=None):
    
    x, y = data[[variable, category]].T.values
    corr = phik_from_array(x, y, num_vars=['x'])
    outsig = outlier_significance_from_array(x, y, num_vars=['x'])
    
    print('Phi_K correlation coefficient:', f'{corr:.2%}')
        
    if corr >= threshold:
        print('There is a strong correlation between\033[1m', variable, '\033[0mand\033[1m', category, '\033[0m\n')
    
    fig, (ax1, ax2) = plt.subplots(1, 2, figsize=plotsize)
    
    colors = colors if len(data[category].unique()) == 2 else None
    alpha = 0.5 if len(data[category].unique()) == 2 else 1
    
    sns.boxplot(x=category, y=variable, data=data, ax=ax1, 
                showmeans=True, meanline=True, palette=colors, width=0.3,
                flierprops=dict(marker='o', markerfacecolor='red', markeredgecolor='white', alpha=alpha),
                meanprops=dict(linestyle='-', linewidth=2, color='orange'),
                medianprops=dict(linestyle='-', linewidth=2, color='white'), 
                boxprops=dict(linewidth=0, alpha=0.7))
    
    ax1.set(ylim=limits)
    
    sns.heatmap(outsig, ax=ax2, annot=True, fmt='.2f', cmap='RdYlGn', cbar_kws={'shrink': 0.8}, 
                center=0, square=True, linewidths=0.1, linecolor='white')
    
    plt.yticks(rotation=0)
    
    plt.show()
    
import phik
import ppscore as pps

def correlation_matrix(data, variables, target=None, method='phik', plotsize=(11,11)):
    cols = variables + [target] if target != None else variables
    
    if method == 'phik':
        corrs = data[cols].phik_matrix()
        print('\n\033[1mPhi_K Correlation Matrix:\033[0m')
    else:
        corrs = pps.matrix(data[cols]).pivot(columns='x', index='y', values='ppscore')
        print('\033[1mPredictive Power Score Matrix:\033[0m')
        
    fig, ax = plt.subplots(figsize=plotsize)
    ax = sns.heatmap(corrs, annot=True, fmt='.1%', cmap='RdYlGn', cbar_kws={'shrink': 0.8}, 
                     vmin=0, center=0.5, vmax=1, square=True, linewidths=0.1, linecolor='white')
    plt.show()
    
from statsmodels.tools.tools import add_constant
from statsmodels.stats.outliers_influence import variance_inflation_factor

def vif(data, variables, style=True):
    # Add constant to the GLM variables
    X = add_constant(data[variables])
    vif_values = [variance_inflation_factor(X.values, i) for i in range(1, X.shape[1])]
    vif_df = pd.DataFrame({'Variable': variables, 'VIF': vif_values})
    vif_df = vif_df.sort_values('VIF', ascending=False).reset_index(drop=True)
    vif_df.index += 1

    if style:
        vif_df = vif_df.style.format({'VIF': '{:,.2f}'})
        
    return vif_df

In [12]:
df.head()

Transaction_ID        Transaction_Date Transaction_Type  Transaction_Amount  \
0        TX00002 2018-01-01 01:48:50.951              T08             50000.0   
1        TX00004 2018-01-01 09:08:52.666              T01           1000000.0   
2        TX00005 2018-01-01 09:08:52.666              T15           1000000.0   
3        TX00006 2018-01-01 09:45:55.969              T15           1000000.0   
4        TX00007 2018-01-01 23:41:59.228              T10           2500000.0   

      CC_ID Card_Type  Card_Holder  Channel_ID Merchant_ID Country_ID  \
0  CCID5563      CC11            2           1       M0001      CTY06   
1  CCID4598      CC08            2           1       M0001      CTY06   
2  CCID2839      CC08            2           1       M0001      CTY06   
3  CCID2968      CC08            2           1       M0001      CTY06   
4  CCID0176      CC12            2           1       M0001      CTY06   

     City_ID EDC_Type EDC_Location EDC_Owner  Average_Transaction_Amount  \
0  CTY06-133  EDC0885     LEDC3703  OEDC0377                   661855.03   
1  CTY06-129  EDC0565     LEDC3205  OEDC0377                  2171907.10   
2  CTY06-073  EDC4639     LEDC3081  OEDC0377                  1714437.98   
3  CTY06-129  EDC3918     LEDC1993  OEDC0377                 10163708.23   
4  CTY06-133  EDC2863     LEDC2062  OEDC0377                   690066.65   

   Maximum_Transaction_Amount  Minimum_Transaction_Amount  \
0                  11000000.0                     24212.0   
1                  28555000.0                    100000.0   
2                   8500000.0                        50.0   
3                 100000000.0                     63000.0   
4                   3523000.0                     26500.0   

   Average_Transaction_Frequency  Fraud_Status  
0                           2.91             0  
1                           3.12             1  
2                           3.58             0  
3                           2.57             0  
4                           4.23             0

In [13]:
df.columns

Index(['Transaction_ID', 'Transaction_Date', 'Transaction_Type',
       'Transaction_Amount', 'CC_ID', 'Card_Type', 'Card_Holder', 'Channel_ID',
       'Merchant_ID', 'Country_ID', 'City_ID', 'EDC_Type', 'EDC_Location',
       'EDC_Owner', 'Average_Transaction_Amount', 'Maximum_Transaction_Amount',
       'Minimum_Transaction_Amount', 'Average_Transaction_Frequency',
       'Fraud_Status'],
      dtype='object')

### Binning

In [14]:
df['Transaction_Type'].unique()

array(['T08', 'T01', 'T15', 'T10', 'T03', 'T13', 'T06', 'T04', 'T02',
       'T11', 'T14', 'T05', 'T19', 'T17', 'T20', 'T12', 'T07', 'T09',
       'T18', 'T16'], dtype=object)

In [15]:
df.groupby(['Transaction_Type']).mean().sort_values(by='Transaction_Amount')

Transaction_Amount  Card_Holder  Channel_ID  \
Transaction_Type                                                
T04                     5.276654e+04     2.000000    1.000000   
T12                     1.535198e+05     2.000000    2.000000   
T11                     2.425972e+05     2.000000    2.000000   
T20                     4.897117e+05     2.000000    1.000000   
T02                     6.961329e+05     2.000000    2.000000   
T15                     9.548215e+05     2.000000    1.000000   
T16                     9.677392e+05     2.000000    2.000000   
T01                     9.750735e+05     1.999651    1.001396   
T06                     1.117193e+06     1.002963    4.912593   
T03                     1.218068e+06     2.000000    1.000000   
T07                     1.735714e+06     1.000000    4.714286   
T13                     1.765345e+06     2.000000    1.000000   
T05                     1.968645e+06     2.000000    1.000000   
T18                     2.050000e+06     2.000000    1.000000   
T19                     2.571429e+06     2.000000    1.000000   
T14                     2.648827e+06     2.000000    1.000000   
T08                     3.066989e+06     1.998134    1.007463   
T09                     3.328812e+06     2.000000    1.000000   
T10                     3.870804e+06     2.000000    1.000000   
T17                     6.685025e+06     1.000000    4.925926   

                  Average_Transaction_Amount  Maximum_Transaction_Amount  \
Transaction_Type                                                           
T04                             1.062949e+06                1.004974e+07   
T12                             1.041452e+06                1.165643e+07   
T11                             9.107376e+05                7.775409e+06   
T20                             8.313920e+05                6.084931e+06   
T02                             1.173872e+06                1.179697e+07   
T15                             1.321156e+06                1.173469e+07   
T16                             9.567774e+05                7.475956e+06   
T01                             1.312805e+06                1.223839e+07   
T06                             1.365535e+06                1.150771e+07   
T03                             1.430117e+06                1.270284e+07   
T07                             1.519026e+06                1.386250e+07   
T13                             1.466629e+06                1.292321e+07   
T05                             1.573480e+06                9.146245e+06   
T18                             1.372751e+06                1.300000e+07   
T19                             1.748457e+06                2.364060e+07   
T14                             1.586431e+06                1.258055e+07   
T08                             1.727375e+06                1.466868e+07   
T09                             2.290792e+06                1.756250e+07   
T10                             1.838835e+06                1.651469e+07   
T17                             1.745151e+06                1.205714e+07   

                  Minimum_Transaction_Amount  Average_Transaction_Frequency  \
Transaction_Type                                                              
T04                             36597.167300                       2.399049   
T12                             51884.259740                       2.209740   
T11                             41524.700000                       2.267800   
T20                             49482.310345                       2.155517   
T02                             59608.027967                       2.359803   
T15                             69176.738864                       2.372350   
T16                             39274.500000                       2.288333   
T01                             98921.652128                       2.421546   
T06                             97400.816296                       2.408044   
T03                             64315.524272 

Interval Transaction Amount
0k-1000k
1000k-2000k
2000k-2999k
3000k-3999k
4000k - ....

In [16]:
target='Fraud_Status'

In [17]:
lol=1
for i in df.index:
    if df['Transaction_Amount'][i]>0 and df['Transaction_Amount'][i]<=1000_000:
        df['Transaction_Type'][i]=1
    elif df['Transaction_Amount'][i]>1000_000 and df['Transaction_Amount'][i]<=2000_000:
        df['Transaction_Type'][i]=2
    elif df['Transaction_Amount'][i]>2000_000 and df['Transaction_Amount'][i]<=3000_000:
        df['Transaction_Type'][i]=3
    elif df['Transaction_Amount'][i]>3000_000 and df['Transaction_Amount'][i]<=4000_000:
        df['Transaction_Type'][i]=4
    elif df['Transaction_Amount'][i]>4000_000:
        df['Transaction_Type'][i]=5
    else:
        None

In [18]:
df

Transaction_ID        Transaction_Date Transaction_Type  \
0            TX00002 2018-01-01 01:48:50.951                1   
1            TX00004 2018-01-01 09:08:52.666                1   
2            TX00005 2018-01-01 09:08:52.666                1   
3            TX00006 2018-01-01 09:45:55.969                1   
4            TX00007 2018-01-01 23:41:59.228                3   
...              ...                     ...              ...   
10495        TX13121 2018-12-31 15:47:34.782                5   
10496        TX13122 2018-12-31 15:47:34.782                5   
10497        TX13123 2018-12-31 15:47:34.782                3   
10498        TX13124 2018-12-31 15:47:34.782                2   
10499        TX13125 2018-12-31 22:11:05.961                1   

       Transaction_Amount     CC_ID Card_Type  Card_Holder  Channel_ID  \
0                 50000.0  CCID5563      CC11            2           1   
1               1000000.0  CCID4598      CC08            2           1   
2               1000000.0  CCID2839      CC08            2           1   
3               1000000.0  CCID2968      CC08            2           1   
4               2500000.0  CCID0176      CC12            2           1   
...                   ...       ...       ...          ...         ...   
10495           5000000.0  CCID4018      CC08            2           1   
10496           4800000.0  CCID7476      CC11            2           1   
10497           2500000.0  CCID7625      CC00            2           1   
10498           1100000.0  CCID6508      CC11            2           1   
10499            102500.0  CCID5211      CC11            2           2   

      Merchant_ID Country_ID    City_ID EDC_Type EDC_Location EDC_Owner  \
0           M0001      CTY06  CTY06-133  EDC0885     LEDC3703  OEDC0377   
1           M0001      CTY06  CTY06-129  EDC0565     LEDC3205  OEDC0377   
2           M0001      CTY06  CTY06-073  EDC4639     LEDC3081  OEDC0377   
3           M0001      CTY06  CTY06-129  EDC3918     LEDC1993  OEDC0377   
4           M0001      CTY06  CTY06-133  EDC2863     LEDC2062  OEDC0377   
...           ...        ...        ...      ...          ...       ...   
10495       M0001      CTY06  CTY06-023  EDC0741     LEDC3813  OEDC0377   
10496       M0001      CTY06  CTY06-181  EDC0797     LEDC3826  OEDC0377   
10497       M0001      CTY06  CTY06-023  EDC0587     LEDC3795  OEDC0377   
10498       M0001      CTY06  CTY06-186  EDC0626     LEDC3811  OEDC0377   
10499       M0597      CTY06  CTY06-171  EDC4477     LEDC4583  OEDC0633   

       Average_Transaction_Amount  Maximum_Transaction_Amount  \
0                       661855.03                  11000000.0   
1                      2171907.10                  28555000.0   
2                      1714437.98                   8500000.0   
3                     10163708.23                 100000000.0   
4                       690066.65                   3523000.0   
...                           ...                         ...   
10495                  1667486.67                  20000000.0   
10496                  2530285.33                   5000000.0   
10497                  1225000.00                  10000000.0   
10498                   820036.79                   4000000.0   
10499                   571282.15                   5000000.0   

       Minimum_Transaction_Amount  Average_Transaction_Frequency  Fraud_Status  
0                         24212.0                           2.91             0  
1                        100000.0                           3.12             1  
2                            50.0                           3.58             0  
3                         63000.0                           2.57             0  
4                         26500.0                           4.23             0  
...                           ...                            ...           ...  
10495                     50000.0                           4.15             0  
10496 

In [19]:
target_pivot(df=df, var='Transaction_Type', target=target, count='Transaction_ID')

P-value: 0.00%
Conclusion: There is a statistically significant association between Transaction_Type and Fraud_Status 

The differences between the observed counts and the expected counts:


Fraud_Status          0      1
Transaction_Type              
1                 202.6 -202.6
2                -144.6  144.6
3                 -37.8   37.8
4                   3.3   -3.3
5                 -23.5   23.5

Pivot table between variable Transaction_Type and Fraud_Status (in percent):


In [20]:
a=df.groupby(['Card_Type'])
x=a[['Maximum_Transaction_Amount']].describe()
x

Maximum_Transaction_Amount                                          \
                               count          mean           std         min   
Card_Type                                                                      
CC00                          1260.0  8.828848e+06  9.274332e+06    300000.0   
CC01                           155.0  7.527955e+06  8.910502e+06    500000.0   
CC02                           157.0  2.713870e+07  2.455402e+07   1000000.0   
CC03                            20.0  1.302905e+07  1.601625e+07    500000.0   
CC04                           237.0  1.235085e+07  1.302443e+07    500000.0   
CC05                           145.0  8.449858e+06  1.118061e+07    500000.0   
CC06                             7.0  1.384479e+07  1.881146e+07   1500000.0   
CC07                             1.0  1.250000e+07           NaN  12500000.0   
CC08                          2106.0  2.744601e+07  2.571725e+07    700000.0   
CC09                          1379.0  5.227493e+06  5.554187e+06     38000.0   
CC10                          1092.0  4.652571e+06  6.384819e+06    100000.0   
CC11                          3835.0  9.659447e+06  9.627690e+06    243000.0   
CC12                            54.0  7.904587e+06  8.975019e+06    750000.0   
CC13                            36.0  6.289568e+06  9.231345e+06    100000.0   

                                                            
                  25%         50%         75%          max  
Card_Type                                                   
CC00        2500000.0   5500000.0  10291000.0   58090000.0  
CC01        2500000.0   4480000.0   9000000.0   50000000.0  
CC02        7480000.0  20000000.0  50000000.0  100000000.0  
CC03        1812500.0   5000000.0  20000000.0   50000000.0  
CC04        2500000.0   6000000.0  20000000.0   75000000.0  
CC05        2500000.0   5000000.0  10000000.0  100000000.0  
CC06        3150000.0   3813500.0  17650000.0   50000000.0  
CC07       12500000.0  12500000.0  12500000.0   12500000.0  
CC08        8000000.0  20000000.0  40000000.0  100000000.0  
CC09        2000000.0   3000000.0   6339450.0   56161050.0  
CC10        1452250.0   2500000.0   5000000.0   69750000.0  
CC11        2700000.0   7000000.0  12204175.5   69750000.0  
CC12        2350000.0   4500000.0   9875000.0   46000000.0  
CC13        1705132.5   2500000.0   6250000.0   50000000.0

In [21]:
#There is a weird sequence there..
df=df.assign(Card_Type_By_Categories='NAN')
for i in df.index:
    if df['Card_Type'][i]=='CC00' or df['Card_Type'][i]=='CC01'or df['Card_Type'][i]=='CC02':
        df['Card_Type_By_Categories'][i]=1
    elif df['Card_Type'][i]=='CC03' or df['Card_Type'][i]=='CC04'or df['Card_Type'][i]=='CC05':
        df['Card_Type_By_Categories'][i]=2
    elif df['Card_Type'][i]=='CC06' or df['Card_Type'][i]=='CC07'or df['Card_Type'][i]=='CC08':
        df['Card_Type_By_Categories'][i]=3
    elif df['Card_Type'][i]=='CC09' or df['Card_Type'][i]=='CC10'or df['Card_Type'][i]=='CC11':
        df['Card_Type_By_Categories'][i]=4
    elif df['Card_Type'][i]=='CC12' or df['Card_Type'][i]=='CC13':
        df['Card_Type_By_Categories'][i]=4    
    else:
        None

In [22]:
df

Transaction_ID        Transaction_Date Transaction_Type  \
0            TX00002 2018-01-01 01:48:50.951                1   
1            TX00004 2018-01-01 09:08:52.666                1   
2            TX00005 2018-01-01 09:08:52.666                1   
3            TX00006 2018-01-01 09:45:55.969                1   
4            TX00007 2018-01-01 23:41:59.228                3   
...              ...                     ...              ...   
10495        TX13121 2018-12-31 15:47:34.782                5   
10496        TX13122 2018-12-31 15:47:34.782                5   
10497        TX13123 2018-12-31 15:47:34.782                3   
10498        TX13124 2018-12-31 15:47:34.782                2   
10499        TX13125 2018-12-31 22:11:05.961                1   

       Transaction_Amount     CC_ID Card_Type  Card_Holder  Channel_ID  \
0                 50000.0  CCID5563      CC11            2           1   
1               1000000.0  CCID4598      CC08            2           1   
2               1000000.0  CCID2839      CC08            2           1   
3               1000000.0  CCID2968      CC08            2           1   
4               2500000.0  CCID0176      CC12            2           1   
...                   ...       ...       ...          ...         ...   
10495           5000000.0  CCID4018      CC08            2           1   
10496           4800000.0  CCID7476      CC11            2           1   
10497           2500000.0  CCID7625      CC00            2           1   
10498           1100000.0  CCID6508      CC11            2           1   
10499            102500.0  CCID5211      CC11            2           2   

      Merchant_ID Country_ID    City_ID EDC_Type EDC_Location EDC_Owner  \
0           M0001      CTY06  CTY06-133  EDC0885     LEDC3703  OEDC0377   
1           M0001      CTY06  CTY06-129  EDC0565     LEDC3205  OEDC0377   
2           M0001      CTY06  CTY06-073  EDC4639     LEDC3081  OEDC0377   
3           M0001      CTY06  CTY06-129  EDC3918     LEDC1993  OEDC0377   
4           M0001      CTY06  CTY06-133  EDC2863     LEDC2062  OEDC0377   
...           ...        ...        ...      ...          ...       ...   
10495       M0001      CTY06  CTY06-023  EDC0741     LEDC3813  OEDC0377   
10496       M0001      CTY06  CTY06-181  EDC0797     LEDC3826  OEDC0377   
10497       M0001      CTY06  CTY06-023  EDC0587     LEDC3795  OEDC0377   
10498       M0001      CTY06  CTY06-186  EDC0626     LEDC3811  OEDC0377   
10499       M0597      CTY06  CTY06-171  EDC4477     LEDC4583  OEDC0633   

       Average_Transaction_Amount  Maximum_Transaction_Amount  \
0                       661855.03                  11000000.0   
1                      2171907.10                  28555000.0   
2                      1714437.98                   8500000.0   
3                     10163708.23                 100000000.0   
4                       690066.65                   3523000.0   
...                           ...                         ...   
10495                  1667486.67                  20000000.0   
10496                  2530285.33                   5000000.0   
10497                  1225000.00                  10000000.0   
10498                   820036.79                   4000000.0   
10499                   571282.15                   5000000.0   

       Minimum_Transaction_Amount  Average_Transaction_Frequency  \
0                         24212.0                           2.91   
1                        100000.0                           3.12   
2                            50.0                           3.58   
3                         63000.0                           2.57   
4                         26500.0                           4.23   
...                           ...                            ...   
10495                     50000.0                           4.15   
10496                   1000000.0                           1.64   
10497                    100000.0         

In [23]:
target_pivot(df=df, var='Card_Type_By_Categories', target=target, count='Transaction_ID')

P-value: 0.00%
Conclusion: There is a statistically significant association between Card_Type_By_Categories and Fraud_Status 

The differences between the observed counts and the expected counts:


Fraud_Status                0     1
Card_Type_By_Categories            
1                       -21.9  21.9
2                       -21.6  21.6
3                        42.0 -42.0
4                         1.6  -1.6

Pivot table between variable Card_Type_By_Categories and Fraud_Status (in percent):


In [41]:
target_pivot(df=df, var='Card_Holder', target=target, count='Transaction_ID')

P-value: 0.00%
Conclusion: There is a statistically significant association between Card_Holder and Fraud_Status 

The differences between the observed counts and the expected counts:


Fraud_Status      0      1
Card_Holder               
1            -227.6  227.6
2             227.6 -227.6

Pivot table between variable Card_Holder and Fraud_Status (in percent):


In [42]:
target_pivot(df=df, var='Channel_ID', target=target, count='Transaction_ID')

P-value: nan%
Conclusion: There is NOT enough evidence to conclude that Channel_ID and Fraud_Status are associated

Pivot table between variable Channel_ID and Fraud_Status (in percent):


In [43]:
category_counts(df, col='Merchant_ID', header=None, decimal=1, asc=False, top=10000, style=True) #Make into M0001 and mno M0001

In [44]:
for i in df.index:
    if df['Merchant_ID'][i]!= 'M0001':
        df['Merchant_ID'][i]= 0
    elif df['Merchant_ID'][i]== 'M0001':
        df['Merchant_ID'][i]= 1

In [45]:
df

Transaction_ID        Transaction_Date Transaction_Type  \
0            TX00002 2018-01-01 01:48:50.951                1   
1            TX00004 2018-01-01 09:08:52.666                1   
2            TX00005 2018-01-01 09:08:52.666                1   
3            TX00006 2018-01-01 09:45:55.969                1   
4            TX00007 2018-01-01 23:41:59.228                3   
...              ...                     ...              ...   
10495        TX13121 2018-12-31 15:47:34.782                5   
10496        TX13122 2018-12-31 15:47:34.782                5   
10497        TX13123 2018-12-31 15:47:34.782                3   
10498        TX13124 2018-12-31 15:47:34.782                2   
10499        TX13125 2018-12-31 22:11:05.961                1   

       Transaction_Amount     CC_ID Card_Type  Card_Holder  Channel_ID  \
0                 50000.0  CCID5563      CC11            2           1   
1               1000000.0  CCID4598      CC08            2           1   
2               1000000.0  CCID2839      CC08            2           1   
3               1000000.0  CCID2968      CC08            2           1   
4               2500000.0  CCID0176      CC12            2           1   
...                   ...       ...       ...          ...         ...   
10495           5000000.0  CCID4018      CC08            2           1   
10496           4800000.0  CCID7476      CC11            2           1   
10497           2500000.0  CCID7625      CC00            2           1   
10498           1100000.0  CCID6508      CC11            2           1   
10499            102500.0  CCID5211      CC11            2           2   

      Merchant_ID Country_ID City_ID EDC_Type EDC_Location EDC_Owner  \
0               0          1       0  EDC0885     LEDC3703         1   
1               0          1       0  EDC0565     LEDC3205         1   
2               0          1       0  EDC4639     LEDC3081         1   
3               0          1       0  EDC3918     LEDC1993         1   
4               0          1       0  EDC2863     LEDC2062         1   
...           ...        ...     ...      ...          ...       ...   
10495           0          1       1  EDC0741     LEDC3813         1   
10496           0          1       0  EDC0797     LEDC3826         1   
10497           0          1       1  EDC0587     LEDC3795         1   
10498           0          1       0  EDC0626     LEDC3811         1   
10499           0          1       0  EDC4477     LEDC4583         0   

       Average_Transaction_Amount  Maximum_Transaction_Amount  \
0                       661855.03                  11000000.0   
1                      2171907.10                  28555000.0   
2                      1714437.98                   8500000.0   
3                     10163708.23                 100000000.0   
4                       690066.65                   3523000.0   
...                           ...                         ...   
10495                  1667486.67                  20000000.0   
10496                  2530285.33                   5000000.0   
10497                  1225000.00                  10000000.0   
10498                   820036.79                   4000000.0   
10499                   571282.15                   5000000.0   

       Minimum_Transaction_Amount  Average_Transaction_Frequency  \
0                         24212.0                           2.91   
1                        100000.0                           3.12   
2                            50.0                           3.58   
3                         63000.0                           2.57   
4                         26500.0                           4.23   
...                           ...                            ...   
10495                     50000.0                           4.15   
10496                   1000000.0                           1.64   
10497                    100000.0                           1.97   
10498     

In [46]:
target_pivot(df=df, var='Merchant_ID', target=target, count='Transaction_ID')

P-value: 100.00%
Conclusion: There is NOT enough evidence to conclude that Merchant_ID and Fraud_Status are associated

Pivot table between variable Merchant_ID and Fraud_Status (in percent):


In [47]:
category_counts(df, col='Country_ID', header=None, decimal=1, asc=False, top=10000, style=True) #Make into M0001 and mno M0001

In [48]:
for i in df.index:
    if df['Country_ID'][i]!= 'CTY06':
        df['Country_ID'][i]= 0
    elif df['Country_ID'][i]== 'CTY06':
        df['Country_ID'][i]= 1

In [49]:
target_pivot(df=df, var='Country_ID', target=target, count='Transaction_ID')

P-value: 100.00%
Conclusion: There is NOT enough evidence to conclude that Country_ID and Fraud_Status are associated

Pivot table between variable Country_ID and Fraud_Status (in percent):


In [50]:
df.head()

Transaction_ID        Transaction_Date Transaction_Type  Transaction_Amount  \
0        TX00002 2018-01-01 01:48:50.951                1             50000.0   
1        TX00004 2018-01-01 09:08:52.666                1           1000000.0   
2        TX00005 2018-01-01 09:08:52.666                1           1000000.0   
3        TX00006 2018-01-01 09:45:55.969                1           1000000.0   
4        TX00007 2018-01-01 23:41:59.228                3           2500000.0   

      CC_ID Card_Type  Card_Holder  Channel_ID Merchant_ID Country_ID City_ID  \
0  CCID5563      CC11            2           1           0          0       0   
1  CCID4598      CC08            2           1           0          0       0   
2  CCID2839      CC08            2           1           0          0       0   
3  CCID2968      CC08            2           1           0          0       0   
4  CCID0176      CC12            2           1           0          0       0   

  EDC_Type EDC_Location EDC_Owner  Average_Transaction_Amount  \
0  EDC0885     LEDC3703         1                   661855.03   
1  EDC0565     LEDC3205         1                  2171907.10   
2  EDC4639     LEDC3081         1                  1714437.98   
3  EDC3918     LEDC1993         1                 10163708.23   
4  EDC2863     LEDC2062         1                   690066.65   

   Maximum_Transaction_Amount  Minimum_Transaction_Amount  \
0                  11000000.0                     24212.0   
1                  28555000.0                    100000.0   
2                   8500000.0                        50.0   
3                 100000000.0                     63000.0   
4                   3523000.0                     26500.0   

   Average_Transaction_Frequency  Fraud_Status Card_Type_By_Categories  
0                           2.91             0                       4  
1                           3.12             1                       3  
2                           3.58             0                       3  
3                           2.57             0                       3  
4                           4.23             0                       4

In [51]:
category_counts(df, col='City_ID', header=None, decimal=1, asc=False, top=10000, style=True) #Make into M0001 and mno M0001

In [52]:
for i in df.index:
    if df['City_ID'][i]== 'CTY06-023' or df['Country_ID'][i]== 'CTY06-133' or df['Country_ID'][i]== 'CTY06-181':
        df['City_ID'][i]= 1
    else:
        df['City_ID'][i]= 0

In [53]:
target_pivot(df=df, var='City_ID', target=target, count='Transaction_ID')

P-value: 100.00%
Conclusion: There is NOT enough evidence to conclude that City_ID and Fraud_Status are associated

Pivot table between variable City_ID and Fraud_Status (in percent):


In [54]:
df

Transaction_ID        Transaction_Date Transaction_Type  \
0            TX00002 2018-01-01 01:48:50.951                1   
1            TX00004 2018-01-01 09:08:52.666                1   
2            TX00005 2018-01-01 09:08:52.666                1   
3            TX00006 2018-01-01 09:45:55.969                1   
4            TX00007 2018-01-01 23:41:59.228                3   
...              ...                     ...              ...   
10495        TX13121 2018-12-31 15:47:34.782                5   
10496        TX13122 2018-12-31 15:47:34.782                5   
10497        TX13123 2018-12-31 15:47:34.782                3   
10498        TX13124 2018-12-31 15:47:34.782                2   
10499        TX13125 2018-12-31 22:11:05.961                1   

       Transaction_Amount     CC_ID Card_Type  Card_Holder  Channel_ID  \
0                 50000.0  CCID5563      CC11            2           1   
1               1000000.0  CCID4598      CC08            2           1   
2               1000000.0  CCID2839      CC08            2           1   
3               1000000.0  CCID2968      CC08            2           1   
4               2500000.0  CCID0176      CC12            2           1   
...                   ...       ...       ...          ...         ...   
10495           5000000.0  CCID4018      CC08            2           1   
10496           4800000.0  CCID7476      CC11            2           1   
10497           2500000.0  CCID7625      CC00            2           1   
10498           1100000.0  CCID6508      CC11            2           1   
10499            102500.0  CCID5211      CC11            2           2   

      Merchant_ID Country_ID City_ID EDC_Type EDC_Location EDC_Owner  \
0               0          0       0  EDC0885     LEDC3703         1   
1               0          0       0  EDC0565     LEDC3205         1   
2               0          0       0  EDC4639     LEDC3081         1   
3               0          0       0  EDC3918     LEDC1993         1   
4               0          0       0  EDC2863     LEDC2062         1   
...           ...        ...     ...      ...          ...       ...   
10495           0          0       0  EDC0741     LEDC3813         1   
10496           0          0       0  EDC0797     LEDC3826         1   
10497           0          0       0  EDC0587     LEDC3795         1   
10498           0          0       0  EDC0626     LEDC3811         1   
10499           0          0       0  EDC4477     LEDC4583         0   

       Average_Transaction_Amount  Maximum_Transaction_Amount  \
0                       661855.03                  11000000.0   
1                      2171907.10                  28555000.0   
2                      1714437.98                   8500000.0   
3                     10163708.23                 100000000.0   
4                       690066.65                   3523000.0   
...                           ...                         ...   
10495                  1667486.67                  20000000.0   
10496                  2530285.33                   5000000.0   
10497                  1225000.00                  10000000.0   
10498                   820036.79                   4000000.0   
10499                   571282.15                   5000000.0   

       Minimum_Transaction_Amount  Average_Transaction_Frequency  \
0                         24212.0                           2.91   
1                        100000.0                           3.12   
2                            50.0                           3.58   
3                         63000.0                           2.57   
4                         26500.0                           4.23   
...                           ...                            ...   
10495                     50000.0                           4.15   
10496                   1000000.0                           1.64   
10497                    100000.0                           1.97   
10498     

In [55]:
category_counts(df, col='EDC_Owner', header=None, decimal=1, asc=False, top=10000, style=True) #Make into M0001 and mno M0001

In [56]:
for i in df.index:
    if df['EDC_Owner'][i]== 'OEDC0377':
        df['EDC_Owner'][i]= 1
    else:
        df['EDC_Owner'][i]= 0

In [57]:
target_pivot(df=df, var='EDC_Owner', target=target, count='Transaction_ID')

P-value: 100.00%
Conclusion: There is NOT enough evidence to conclude that EDC_Owner and Fraud_Status are associated

Pivot table between variable EDC_Owner and Fraud_Status (in percent):


In [58]:
df

Transaction_ID        Transaction_Date Transaction_Type  \
0            TX00002 2018-01-01 01:48:50.951                1   
1            TX00004 2018-01-01 09:08:52.666                1   
2            TX00005 2018-01-01 09:08:52.666                1   
3            TX00006 2018-01-01 09:45:55.969                1   
4            TX00007 2018-01-01 23:41:59.228                3   
...              ...                     ...              ...   
10495        TX13121 2018-12-31 15:47:34.782                5   
10496        TX13122 2018-12-31 15:47:34.782                5   
10497        TX13123 2018-12-31 15:47:34.782                3   
10498        TX13124 2018-12-31 15:47:34.782                2   
10499        TX13125 2018-12-31 22:11:05.961                1   

       Transaction_Amount     CC_ID Card_Type  Card_Holder  Channel_ID  \
0                 50000.0  CCID5563      CC11            2           1   
1               1000000.0  CCID4598      CC08            2           1   
2               1000000.0  CCID2839      CC08            2           1   
3               1000000.0  CCID2968      CC08            2           1   
4               2500000.0  CCID0176      CC12            2           1   
...                   ...       ...       ...          ...         ...   
10495           5000000.0  CCID4018      CC08            2           1   
10496           4800000.0  CCID7476      CC11            2           1   
10497           2500000.0  CCID7625      CC00            2           1   
10498           1100000.0  CCID6508      CC11            2           1   
10499            102500.0  CCID5211      CC11            2           2   

      Merchant_ID Country_ID City_ID EDC_Type EDC_Location EDC_Owner  \
0               0          0       0  EDC0885     LEDC3703         0   
1               0          0       0  EDC0565     LEDC3205         0   
2               0          0       0  EDC4639     LEDC3081         0   
3               0          0       0  EDC3918     LEDC1993         0   
4               0          0       0  EDC2863     LEDC2062         0   
...           ...        ...     ...      ...          ...       ...   
10495           0          0       0  EDC0741     LEDC3813         0   
10496           0          0       0  EDC0797     LEDC3826         0   
10497           0          0       0  EDC0587     LEDC3795         0   
10498           0          0       0  EDC0626     LEDC3811         0   
10499           0          0       0  EDC4477     LEDC4583         0   

       Average_Transaction_Amount  Maximum_Transaction_Amount  \
0                       661855.03                  11000000.0   
1                      2171907.10                  28555000.0   
2                      1714437.98                   8500000.0   
3                     10163708.23                 100000000.0   
4                       690066.65                   3523000.0   
...                           ...                         ...   
10495                  1667486.67                  20000000.0   
10496                  2530285.33                   5000000.0   
10497                  1225000.00                  10000000.0   
10498                   820036.79                   4000000.0   
10499                   571282.15                   5000000.0   

       Minimum_Transaction_Amount  Average_Transaction_Frequency  \
0                         24212.0                           2.91   
1                        100000.0                           3.12   
2                            50.0                           3.58   
3                         63000.0                           2.57   
4                         26500.0                           4.23   
...                           ...                            ...   
10495                     50000.0                           4.15   
10496                   1000000.0                           1.64   
10497                    100000.0                           1.97   
10498     

In [59]:
category_counts(df, col='EDC_Location', header=None, decimal=1, asc=False, top=10000, style=True) #Make into M0001 and mno M0001

In [60]:
df2=df.drop(['EDC_Location','EDC_Type','Transaction_ID'],axis=1)

In [61]:
df2

Transaction_Date Transaction_Type  Transaction_Amount     CC_ID  \
0     2018-01-01 01:48:50.951                1             50000.0  CCID5563   
1     2018-01-01 09:08:52.666                1           1000000.0  CCID4598   
2     2018-01-01 09:08:52.666                1           1000000.0  CCID2839   
3     2018-01-01 09:45:55.969                1           1000000.0  CCID2968   
4     2018-01-01 23:41:59.228                3           2500000.0  CCID0176   
...                       ...              ...                 ...       ...   
10495 2018-12-31 15:47:34.782                5           5000000.0  CCID4018   
10496 2018-12-31 15:47:34.782                5           4800000.0  CCID7476   
10497 2018-12-31 15:47:34.782                3           2500000.0  CCID7625   
10498 2018-12-31 15:47:34.782                2           1100000.0  CCID6508   
10499 2018-12-31 22:11:05.961                1            102500.0  CCID5211   

      Card_Type  Card_Holder  Channel_ID Merchant_ID Country_ID City_ID  \
0          CC11            2           1           0          0       0   
1          CC08            2           1           0          0       0   
2          CC08            2           1           0          0       0   
3          CC08            2           1           0          0       0   
4          CC12            2           1           0          0       0   
...         ...          ...         ...         ...        ...     ...   
10495      CC08            2           1           0          0       0   
10496      CC11            2           1           0          0       0   
10497      CC00            2           1           0          0       0   
10498      CC11            2           1           0          0       0   
10499      CC11            2           2           0          0       0   

      EDC_Owner  Average_Transaction_Amount  Maximum_Transaction_Amount  \
0             0                   661855.03                  11000000.0   
1             0                  2171907.10                  28555000.0   
2             0                  1714437.98                   8500000.0   
3             0                 10163708.23                 100000000.0   
4             0                   690066.65                   3523000.0   
...         ...                         ...                         ...   
10495         0                  1667486.67                  20000000.0   
10496         0                  2530285.33                   5000000.0   
10497         0                  1225000.00                  10000000.0   
10498         0                   820036.79                   4000000.0   
10499         0                   571282.15                   5000000.0   

       Minimum_Transaction_Amount  Average_Transaction_Frequency  \
0                         24212.0                           2.91   
1                        100000.0                           3.12   
2                            50.0                           3.58   
3                         63000.0                           2.57   
4                         26500.0                           4.23   
...                           ...                            ...   
10495                     50000.0                           4.15   
10496                   1000000.0                           1.64   
10497                    100000.0                           1.97   
10498                     50000.0                           3.16   
10499                     25000.0                           2.36   

       Fraud_Status Card_Type_By_Categories  
0                 0                       4  
1                 1                       3  
2                 0                       3  
3                 0                       3  
4                 0                       4  
...             ...                     ...  
10495             0                       3  
10496             0                       4  
10497             0

In [62]:
df2['Transaction_Date'] = pd.to_datetime(df2['Transaction_Date']).dt.day
df2

Transaction_Date Transaction_Type  Transaction_Amount     CC_ID  \
0                     1                1             50000.0  CCID5563   
1                     1                1           1000000.0  CCID4598   
2                     1                1           1000000.0  CCID2839   
3                     1                1           1000000.0  CCID2968   
4                     1                3           2500000.0  CCID0176   
...                 ...              ...                 ...       ...   
10495                31                5           5000000.0  CCID4018   
10496                31                5           4800000.0  CCID7476   
10497                31                3           2500000.0  CCID7625   
10498                31                2           1100000.0  CCID6508   
10499                31                1            102500.0  CCID5211   

      Card_Type  Card_Holder  Channel_ID Merchant_ID Country_ID City_ID  \
0          CC11            2           1           0          0       0   
1          CC08            2           1           0          0       0   
2          CC08            2           1           0          0       0   
3          CC08            2           1           0          0       0   
4          CC12            2           1           0          0       0   
...         ...          ...         ...         ...        ...     ...   
10495      CC08            2           1           0          0       0   
10496      CC11            2           1           0          0       0   
10497      CC00            2           1           0          0       0   
10498      CC11            2           1           0          0       0   
10499      CC11            2           2           0          0       0   

      EDC_Owner  Average_Transaction_Amount  Maximum_Transaction_Amount  \
0             0                   661855.03                  11000000.0   
1             0                  2171907.10                  28555000.0   
2             0                  1714437.98                   8500000.0   
3             0                 10163708.23                 100000000.0   
4             0                   690066.65                   3523000.0   
...         ...                         ...                         ...   
10495         0                  1667486.67                  20000000.0   
10496         0                  2530285.33                   5000000.0   
10497         0                  1225000.00                  10000000.0   
10498         0                   820036.79                   4000000.0   
10499         0                   571282.15                   5000000.0   

       Minimum_Transaction_Amount  Average_Transaction_Frequency  \
0                         24212.0                           2.91   
1                        100000.0                           3.12   
2                            50.0                           3.58   
3                         63000.0                           2.57   
4                         26500.0                           4.23   
...                           ...                            ...   
10495                     50000.0                           4.15   
10496                   1000000.0                           1.64   
10497                    100000.0                           1.97   
10498                     50000.0                           3.16   
10499                     25000.0                           2.36   

       Fraud_Status Card_Type_By_Categories  
0                 0                       4  
1                 1                       3  
2                 0                       3  
3                 0                       3  
4                 0                       4  
...             ...                     ...  
10495             0                       3  
10496             0                       4  
10497             0                       1  
10498             0                    

### Part 2

In [63]:
from math import sqrt
from sklearn import metrics
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier, export_graphviz
from sklearn.metrics import mean_squared_error
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn import svm
from keras.models import Sequential
from keras.layers import Dense
import statsmodels.api as sm
from tensorflow.keras.wrappers.scikit_learn import KerasClassifier

from sklearn.metrics import classification_report,confusion_matrix
from sklearn.metrics import r2_score
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GridSearchCV

%matplotlib inline

In [64]:
TargetVariable='Fraud_Status'
Predictors=['Transaction_Date', 'Transaction_Type', 'Transaction_Amount',
      'Card_Holder', 'Channel_ID', 'Merchant_ID', 'Country_ID',
       'City_ID', 'EDC_Owner',
       'Average_Transaction_Amount', 'Maximum_Transaction_Amount',
       'Minimum_Transaction_Amount', 'Average_Transaction_Frequency','Card_Type_By_Categories']

X=df2[Predictors]
y=df2[TargetVariable]

x_train, x_test, y_train, y_test = train_test_split(X,y, test_size=0.30, random_state=101)

#### Decision Tree Grid Search

In [42]:
tree_para = {'criterion':['gini','entropy','log_loss'],'max_depth':[4,5,6,7,8,9,10,11,12,15,20,30,40,50,70,90,120,150]}

clf = GridSearchCV(DecisionTreeClassifier(), tree_para, cv=10,scoring='f1')

In [43]:
clf.fit(X, y)

GridSearchCV(cv=10, estimator=DecisionTreeClassifier(),
             param_grid={'criterion': ['gini', 'entropy', 'log_loss'],
                         'max_depth': [4, 5, 6, 7, 8, 9, 10, 11, 12, 15, 20, 30,
                                       40, 50, 70, 90, 120, 150]},
             scoring='f1')

In [44]:
clf.cv_results_

{'mean_fit_time': array([0.01845319, 0.0209193 , 0.02319598, 0.02590277, 0.02879066,
        0.03164134, 0.03354709, 0.03543692, 0.0375304 , 0.0425065 ,
        0.04628572, 0.047225  , 0.0473994 , 0.04652269, 0.04730349,
        0.04672129, 0.0466903 , 0.04716887, 0.01972318, 0.02301457,
        0.02629204, 0.02959232, 0.03278346, 0.03606195, 0.03862956,
        0.04089317, 0.04325757, 0.04728355, 0.05010579, 0.05166774,
        0.05188119, 0.0516782 , 0.05204647, 0.05159824, 0.0514833 ,
        0.05168581, 0.01949403, 0.02302878, 0.02624011, 0.02959743,
        0.03319473, 0.03598611, 0.03861239, 0.04085436, 0.04311669,
        0.04735055, 0.05080764, 0.05171478, 0.05170257, 0.05131288,
        0.05158198, 0.05145869, 0.05189326, 0.05154724]),
 'std_fit_time': array([0.00103306, 0.00055157, 0.0004    , 0.00053515, 0.00071402,
        0.00072164, 0.00054672, 0.00046127, 0.00075612, 0.00069399,
        0.00161597, 0.00166316, 0.00142955, 0.00144203, 0.00180741,
        0.00153188, 0.001

In [45]:
clf.best_score_

0.41842343435468815

In [46]:
clf.best_estimator_

DecisionTreeClassifier(criterion='entropy', max_depth=6)

In [76]:
dec = DecisionTreeClassifier(random_state=101,max_depth=7,criterion='entropy')
dec.fit(x_train, y_train)  #fit the model
preddec=dec.predict(x_test)

In [77]:
Accuracy_Values=cross_val_score(dec, X , y, cv=10,scoring='f1')
print('\nAccuracy values for 10-fold Cross Validation:\n',Accuracy_Values)
print('\nFinal Average Accuracy of the model:', round(Accuracy_Values.mean(),2))


Accuracy values for 10-fold Cross Validation:
 [0.26923077 0.35185185 0.27184466 0.34482759 0.5        0.41025641
 0.50847458 0.46153846 0.55855856 0.38297872]

Final Average Accuracy of the model: 0.41


In [78]:
print(classification_report(y_test,preddec))

              precision    recall  f1-score   support

           0       0.95      0.98      0.97      2930
           1       0.58      0.30      0.40       216

    accuracy                           0.94      3146
   macro avg       0.76      0.64      0.68      3146
weighted avg       0.92      0.94      0.93      3146



#### Random Forest Grid Search

In [49]:
forest_para = {'criterion':['gini','entropy'],'max_depth':[4,5,6,7,8,9,10,12,20,40,50,100,200,400],'n_estimators':[500,300,100,50,20,10,5]}

clf2 = GridSearchCV(RandomForestClassifier(), forest_para, cv=10,scoring='f1')

In [50]:
clf2.fit(X, y)

GridSearchCV(cv=10, estimator=RandomForestClassifier(),
             param_grid={'criterion': ['gini', 'entropy'],
                         'max_depth': [4, 5, 6, 7, 8, 9, 10, 12, 20, 40, 50,
                                       100, 200, 400],
                         'n_estimators': [500, 300, 100, 50, 20, 10, 5]},
             scoring='f1')

In [51]:
clf2.cv_results_

{'mean_fit_time': array([1.48872354, 0.89996271, 0.30257864, 0.15613766, 0.06661503,
        0.03722541, 0.02220457, 1.73308308, 1.14642737, 0.36790392,
        0.18029268, 0.07609756, 0.04168835, 0.02479734, 1.90547833,
        1.1481111 , 0.38476601, 0.1948859 , 0.08425684, 0.04776115,
        0.02670083, 2.16302559, 1.32593069, 0.43442409, 0.22821021,
        0.09428713, 0.05033381, 0.0296891 , 2.50386617, 1.36163454,
        0.45774095, 0.23446176, 0.09883528, 0.05235956, 0.03081064,
        2.45541167, 1.47789173, 0.49765511, 0.25248444, 0.10531836,
        0.05641046, 0.03237541, 2.640748  , 1.58199551, 0.53297625,
        0.27081485, 0.11240506, 0.06023204, 0.03388178, 2.94008353,
        1.77480545, 0.59668474, 0.30135422, 0.12516444, 0.06707969,
        0.03720105, 3.50665014, 2.23133714, 0.7426898 , 0.36731691,
        0.14491484, 0.07715113, 0.04258566, 3.63604946, 2.0933085 ,
        0.70020795, 0.35276101, 0.1474787 , 0.07592316, 0.04248652,
        3.49810889, 2.08945203,

In [52]:
clf2.best_score_

0.37228433463467153

In [53]:
clf2.best_estimator_

RandomForestClassifier(max_depth=12, n_estimators=10)

In [54]:
rf = RandomForestClassifier(random_state=101,max_depth=14,criterion='entropy',n_estimators=500)
rf.fit(x_train, y_train)  #fit the model
predrf=rf.predict(x_test)

In [55]:
Accuracy_Values=cross_val_score(rf, X , y, cv=10,scoring='f1')
print('\nAccuracy values for 10-fold Cross Validation:\n',Accuracy_Values)
print('\nFinal Average Accuracy of the model:', round(Accuracy_Values.mean(),2))


Accuracy values for 10-fold Cross Validation:
 [0.27659574 0.40740741 0.24719101 0.2745098  0.38       0.39215686
 0.39215686 0.44444444 0.4        0.28888889]

Final Average Accuracy of the model: 0.35


#### ADABOOST Grid Search

In [63]:
ADABOOST_para = {'n_estimators':[500,300,100,50,20,10,5],'learning_rate':[0.04,0.06,0.1,0.2,0.4,0.8]}
clf3 = GridSearchCV(AdaBoostClassifier(base_estimator=dec), ADABOOST_para, cv=10,scoring='f1')

In [64]:
clf3.fit(X, y)

GridSearchCV(cv=10,
             estimator=AdaBoostClassifier(base_estimator=DecisionTreeClassifier(criterion='entropy',
                                                                                max_depth=7,
                                                                                random_state=101)),
             param_grid={'learning_rate': [0.04, 0.06, 0.1, 0.2, 0.4, 0.8],
                         'n_estimators': [500, 300, 100, 50, 20, 10, 5]},
             scoring='f1')

In [65]:
clf3.cv_results_

{'mean_fit_time': array([17.73009667, 10.48028395,  3.41613743,  1.74415581,  0.69429855,
         0.34231958,  0.1717443 , 17.47676826, 10.28599138,  3.47826562,
         1.69191055,  0.67133071,  0.34126227,  0.17355313, 17.33192425,
         9.9909934 ,  3.36733513,  1.64290559,  0.6609988 ,  0.36837344,
         0.23538895, 17.38939819, 10.288205  ,  3.27429206,  1.65722106,
         0.64273157,  0.33367426,  0.16557298, 17.68404725, 10.01224501,
         3.39482343,  1.64106281,  0.652579  ,  0.3289777 ,  0.16625736,
        18.55517385, 10.66115227,  3.3933327 ,  1.66761873,  0.65617924,
         0.33536081,  0.1882241 ]),
 'std_fit_time': array([0.79602587, 0.38056202, 0.10316613, 0.05994247, 0.04663953,
        0.02055905, 0.0061571 , 0.90335517, 0.36389552, 0.19432601,
        0.06284007, 0.01250185, 0.0096859 , 0.00760308, 1.02652789,
        0.26445495, 0.10085055, 0.02448613, 0.01681905, 0.0430736 ,
        0.03833347, 0.43705009, 0.28638047, 0.0855208 , 0.05208396,
       

In [66]:
clf3.best_score_

0.41614843291545445

In [67]:
clf3.best_estimator_

AdaBoostClassifier(base_estimator=DecisionTreeClassifier(criterion='entropy',
                                                         max_depth=7,
                                                         random_state=101),
                   learning_rate=0.06, n_estimators=10)

In [75]:
ada = AdaBoostClassifier(n_estimators=10, base_estimator=dec ,learning_rate=0.06)
ada.fit(x_train,y_train)
preada=ada.predict(x_test)

NameError: name 'dec' is not defined

In [71]:
Accuracy_Values=cross_val_score(ada, X , y, cv=10,scoring='f1')
print('\nAccuracy values for 10-fold Cross Validation:\n',Accuracy_Values)
print('\nFinal Average Accuracy of the model:', round(Accuracy_Values.mean(),2))


Accuracy values for 10-fold Cross Validation:
 [0.34615385 0.46153846 0.37383178 0.34188034 0.44642857 0.47457627
 0.44067797 0.32727273 0.48148148 0.41121495]

Final Average Accuracy of the model: 0.41


#### SVM Grid Search

In [73]:
svm_para = {'C':[1,3,5,7,10,20,40,100,200,500,1000],'kernel':['rbf','linear','poly','sigmoid'],'degree':[2,3,4,5,6,7,8,9,10],'gamma':['scale','auto']}
clf4 = GridSearchCV(svm.SVC(), svm_para, cv=10,scoring='f1')

In [ ]:
clf4.fit(X, y)

In [ ]:
clf4.cv_results_

In [ ]:
clf4.best_score_

In [ ]:
clf4.best_estimator_

In [80]:
sv = svm.SVC(C=5, kernel='rbf', gamma=0.01)
SVM=sv.fit(x_train,y_train)
predsvm=SVM.predict_proba(x_test)

AttributeError: predict_proba is not available when  probability=False

In [66]:
Accuracy_Values=cross_val_score(SVM, X , y, cv=10)
print('\nAccuracy values for 10-fold Cross Validation:\n',Accuracy_Values)
print('\nFinal Average Accuracy of the model:', round(Accuracy_Values.mean(),2))


Accuracy values for 10-fold Cross Validation:
 [0.9313632  0.9313632  0.92755005 0.9313632  0.93129771 0.93129771
 0.93225191 0.93225191 0.93225191 0.93225191]

Final Average Accuracy of the model: 0.93


In [72]:
TestingDataResults=pd.DataFrame(data=x_test, columns=Predictors)
TestingDataResults[TargetVariable]=y_test
TestingDataResults[('Predicted'+TargetVariable)]=np.round(predsvm)
print(TestingDataResults[[TargetVariable,'Predicted'+TargetVariable]])

      Fraud_Status  PredictedFraud_Status
8302             0                      0
6866             0                      0
7683             0                      0
218              0                      0
9380             0                      0
...            ...                    ...
6631             0                      0
2097             0                      0
8468             0                      0
7587             0                      0
2059             0                      0

[3146 rows x 2 columns]


In [79]:
print(classification_report(y_test,preada))

NameError: name 'preada' is not defined

#### Gradient Boosting Grid Search

In [67]:
X

Transaction_Date Transaction_Type  Transaction_Amount  Card_Holder  \
0                     1                1             50000.0            2   
1                     1                1           1000000.0            2   
2                     1                1           1000000.0            2   
3                     1                1           1000000.0            2   
4                     1                3           2500000.0            2   
...                 ...              ...                 ...          ...   
10495                31                5           5000000.0            2   
10496                31                5           4800000.0            2   
10497                31                3           2500000.0            2   
10498                31                2           1100000.0            2   
10499                31                1            102500.0            2   

       Channel_ID Merchant_ID Country_ID City_ID EDC_Owner  \
0               1           0          0       0         0   
1               1           0          0       0         0   
2               1           0          0       0         0   
3               1           0          0       0         0   
4               1           0          0       0         0   
...           ...         ...        ...     ...       ...   
10495           1           0          0       0         0   
10496           1           0          0       0         0   
10497           1           0          0       0         0   
10498           1           0          0       0         0   
10499           2           0          0       0         0   

       Average_Transaction_Amount  Maximum_Transaction_Amount  \
0                       661855.03                  11000000.0   
1                      2171907.10                  28555000.0   
2                      1714437.98                   8500000.0   
3                     10163708.23                 100000000.0   
4                       690066.65                   3523000.0   
...                           ...                         ...   
10495                  1667486.67                  20000000.0   
10496                  2530285.33                   5000000.0   
10497                  1225000.00                  10000000.0   
10498                   820036.79                   4000000.0   
10499                   571282.15                   5000000.0   

       Minimum_Transaction_Amount  Average_Transaction_Frequency  \
0                         24212.0                           2.91   
1                        100000.0                           3.12   
2                            50.0                           3.58   
3                         63000.0                           2.57   
4                         26500.0                           4.23   
...                           ...                            ...   
10495                     50000.0                           4.15   
10496                   1000000.0                           1.64   
10497                    100000.0                           1.97   
10498                     50000.0                           3.16   
10499                     25000.0                           2.36   

      Card_Type_By_Categories  
0                           4  
1                           3  
2                           3  
3                           3  
4                           4  
...                       ...  
10495                       3  
10496                       4  
10497                       1  
10498                       4  
10499                       4  

[10484 rows x 14 columns]

In [68]:
y

0        0
1        1
2        0
3        0
4        0
        ..
10495    0
10496    0
10497    0
10498    0
10499    0
Name: Fraud_Status, Length: 10484, dtype: int64

In [69]:
predsvm

array([0, 0, 0, ..., 0, 0, 0], dtype=int64)

In [ ]:
sv = svm.SVC(C=5, kernel='rbf', gamma=0.01)
SVM=sv.fit(x_train,y_train)
predsvm=SVM.predict(x_test)